In [37]:
import requests
from datetime import datetime, timedelta
from models.GFW_auth import GFW_auth
import geopandas as gpd
import json
from collections import defaultdict
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import folium
from folium.raster_layers import ImageOverlay
from matplotlib import cm, colors
import matplotlib

In [38]:


def get_fishing_effort_report():
    #To do: poner parametros a esta funcion de: date range, temporal resolution, arte de pesca...
    url="https://gateway.api.globalfishingwatch.org/v3/4wings/report"

    headers=GFW_auth().headers

    fao_21_27_60N_polygon = gpd.read_file("./data/GFW_polygon.geojson")
    geojson_dict = json.loads(fao_21_27_60N_polygon.to_json())
    payload = {
    "geojson": {
        "type": "FeatureCollection",
        "features": [
            {
                "type": "Feature",
                "properties": {},
                "geometry": geojson_dict['features'][0]['geometry']
            }
        ]
    }
}
    
    params = {
        'date-range': '2024-01-01,2025-01-01',
        "spatial-resolution": "LOW",
        "temporal-resolution": "ENTIRE",
        "datasets[0]": "public-global-fishing-effort:latest",
        "format": "JSON",
        "group-by": "VESSEL_ID",
        "filters[0]": "geartype in ('trawlers')"
    }
    response = requests.post(url, params=params, headers=headers, json=payload)

    if response.status_code == 200:
        print("Response Status 200")
        data = response.json()
        return data
    else:
        print("Error:", response.status_code)
        print("Response text:", response.text)

In [39]:
data = get_fishing_effort_report()

Response Status 200


In [40]:
bottom_trawlers = pd.read_csv("./data/strict_bottom_trawlers.csv")
bottom_trawlers_mmsi_list = bottom_trawlers["MMSIstr"].astype(str).to_list()
filtered_df = bottom_trawlers[bottom_trawlers["MMSIstr"] == int("205308000")]
tonnage = filtered_df["Tonnage GT"].iloc[-1]
ME_power = filtered_df["Power of main engine"].iloc[-1]
vessel_name = filtered_df["Name of vessel"].iloc[-1]
print(tonnage)

60.0


In [41]:
ver1=data["entries"][0]['public-global-fishing-effort:v3.0']
location_hours = defaultdict(float)
for entry in ver1:
        if entry.get('mmsi') in bottom_trawlers_mmsi_list:
            mmsi = entry.get('mmsi')
            filtered_df = bottom_trawlers[bottom_trawlers["MMSIstr"] == int(mmsi)]
            tonnage = filtered_df["Tonnage GT"].iloc[-1]
            ME_power = filtered_df["Power of main engine"].iloc[-1]
            vessel_name = filtered_df["Name of vessel"].iloc[-1]
            print(mmsi, vessel_name, ME_power, tonnage)
            key = (entry['lat'], entry['lon'])
            location_hours[key] += entry['hours']

coords = np.array(list(location_hours.keys()))
values = np.array(list(location_hours.values()))

235096987 SAPPHIRE II 597.0 180.0
224314000 PLAYA MENDUIÑA DOS 999.26 1046.0
228172000 IROISE I 249.0 91.62
219001343 BLUE OCEAN 221.0 56.0
245053000 CHRISTIAN KLAAS 221.0 137.0
227485000 CONNEMARA 339.0 115.92
266147000 STRANNEFJORD 478.0 162.0
224162930 CANTABRICO TRES 689.71 352.0
244507000 JACOBA ALIJDA 683.0 208.0
205127000 FRANSON 1200.0 384.0
228436800 LAREDO 734.0 315.0
266274000 KENNEDY 590.0 263.0
266128000 VALKYRIA 220.0 82.0
219031087 CHRISTINA 210.0 65.0
246105000 BRIES 221.0 54.0
263587000 NOVO VIRGEM DA BARCA 1879.0 966.0
220127000 STJERNE 220.0 49.9
227913470 WELSH ROCK 331.0 98.93
246424000 ANNA 677.0 325.0
224011290 POMBO SEIS 724.0 252.0
245473000 GEERTRUID ADRIANA 1103.0 499.0
228236700 LES CALANQUES 497.0 180.18
224105450 CHIRINGUI PRIMERO 358.19 34.13
224047360 BURELES 510.29 223.61
228078700 MARANELLO 400.0 149.62
245836000 AART MAASKANT 1467.0 501.0
205198000 BLUE ANGEL 1200.0 388.0
224324000 BAQUEIRO 429.53 332.0
219023738 EMLI PILEGAARD 746.0 334.8
244299000 J

In [ ]:
# Filter mask: only values > 1
mask = values > 2

# Apply mask to coordinates and values
filtered_coords = coords[mask]
filtered_values = values[mask]

# Split into lat/lon
lats = filtered_coords[:, 0]
lons = filtered_coords[:, 1]

# Create figure with no axes
fig, ax = plt.subplots(figsize=(12, 8))
ax.axis('off')
margin=0.2
ax.set_xlim([lons.min()-margin, lons.max()+margin])
ax.set_ylim([lats.min()-margin, lats.max()+margin])

# Plot colored dots
sc = ax.scatter(
    lons, lats,
    c=filtered_values,
    cmap='plasma',     # Try 'viridis', 'inferno', 'hot', etc.
    s=30,              # Dot size
    edgecolors='none'
)

# Save as transparent PNG
fig.savefig('./maps/dots_colored.png', pad_inches=0, transparent=True)
plt.close(fig)

#for reference folium x PNG
bounds = [
    [lats.min()-margin, lons.min()-margin],
    [lats.max()+margin, lons.max()+margin]
]

# Center map
m = folium.Map(location=[lats.mean(), lons.mean()], zoom_start=6)

# Add satellite basemap with attribution
folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Tiles © Esri — Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
    name='Esri Satellite',
    overlay=False,
    control=True
).add_to(m)


# Add heatmap layer
ImageOverlay(
    image='./maps/dots_colored.png',
    bounds=bounds,
    opacity=0.6,
    interactive=True,
    cross_origin=False
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save or display
m.save('./maps/North_atlantic_fishing_scattermap.html')

In [ ]:

from matplotlib import cm, colors

# Normalize values for colormap
norm = colors.Normalize(vmin=values.min(), vmax=values.max())
colormap = matplotlib.colormaps['plasma']

# Create Folium map centered on mean location
m = folium.Map(location=[coords[:, 0].mean(), coords[:, 1].mean()], zoom_start=6)

# Add satellite basemap
folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Tiles © Esri — Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
    name='Esri Satellite',
    overlay=False,
    control=True
).add_to(m)

# Add colored circle markers
for (lat, lon), val in zip(coords, values):
    rgba = colormap(norm(val))
    hex_color = colors.to_hex(rgba)
    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        color=hex_color,
        fill=True,
        fill_color=hex_color,
        fill_opacity=0.8,
        popup=f"Value: {val:.2f}"
    ).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save map
m.save('./maps/fishing_scattermap.html')